# 量化

In [1]:
import set_env
from pathlib import Path

temp_dir = Path(".temp")
temp_dir.mkdir(exist_ok=True)

In [2]:
from tvm.contrib.msc.core.tools import ToolType
# pylint: disable=import-outside-toplevel
from tvm.contrib.msc.core.tools.quantize import QuantizeStage
from tvm.contrib.msc.core.utils.namespace import MSCFramework

run_type = MSCFramework.MSC
if run_type == MSCFramework.TENSORRT:
    config = {"plan_file": "msc_quantizer.json", "strategys": []}
else:
    op_types = ["nn.conv2d", "msc.conv2d_bias", "msc.linear", "msc.linear_bias"]
    config = {
        "plan_file": "msc_quantizer.json",
        "strategys": [
            {
                "methods": {
                    "input": "gather_maxmin",
                    "output": "gather_maxmin",
                    "weights": "gather_max_per_channel",
                },
                "op_types": op_types,
                "stages": [QuantizeStage.GATHER],
            },
            {
                "methods": {"input": "calibrate_maxmin", "output": "calibrate_maxmin"},
                "op_types": op_types,
                "stages": [QuantizeStage.CALIBRATE],
            },
            {
                "methods": {
                    "input": "quantize_normal",
                    "weights": "quantize_normal",
                    "output": "dequantize_normal",
                },
                "op_types": op_types,
            },
        ],
    }
tools = [{"tool_type": ToolType.QUANTIZER, "tool_config": config}]


In [3]:
from utils import get_model_info, _test_from_torch

_test_from_torch(
    MSCFramework.TVM, tools, 
    get_model_info(MSCFramework.TVM), 
    temp_dir,
    training=False
)

/media/pc/data/lxw/ai/tvm/python/tvm/contrib/msc/framework/torch/codegen/codegen.py:74: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  state_dict = torch.load(folder.relpath(

## 蒸馏

In [4]:
config = {
    "plan_file": "msc_distiller.json",
    "strategys": [
        {
            "methods": {"mark": "loss_lp_norm"},
            "marks": ["loss"],
        },
    ],
}
tools.append({"tool_type": ToolType.DISTILLER, "tool_config": config})

In [5]:
from utils import get_model_info, _test_from_torch

_test_from_torch(
    MSCFramework.TVM, tools, 
    get_model_info(MSCFramework.TVM), 
    temp_dir,
    training=False
)

/media/pc/data/lxw/ai/tvm/python/tvm/contrib/msc/framework/torch/codegen/codegen.py:74: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  state_dict = torch.load(folder.relpath(